#PyTorch Intro - Autoróżniczkowanie i Graf Obliczeń - Laboratorium

Do optymalizacji parametrów (wag) sieci neuronowej podczas treningu modelu wykorzystuje się **metodę stochastycznego spadku wzdłuż gradientu**.
Gradient funkcji straty względem parametrów sieci wyznaczany jest algorytmem **propagacji wstecznej** (*back propagation*).

Sieć neuronową możemy potraktować jak złożoną funkcję mapującą wejściowe dane $x \in \mathcal{X}$ (np. obraz czy sekwencję audio) na wyjście $y \in \mathcal{Y}$ parametryzowaną zestawem parametrów (wag) $\theta$.
$$
f_{\theta}( x ) = y
$$
W przypadku $n$-klasowego klasyfikatora wyjściem z sieci jest wektor $y \in \mathbb{R}^n$ nieznormalizowanych wartości, zwanych logitami, z których możemy wyznaczyć rozkład prawdopodobieństwa klas korzystając z funkcji softmax.

W jednym kroku treningu sieci neuronowych wykonujemy:
1. **Przejście w przód** - przetworzenie zestawu wejściowych danych treningowych przez sieć i wyznaczenie wartości wynikowych $y = f_{\theta}(x)$. Następnie wyznaczenie wartości funkcji straty
$\mathcal{L}$
w oparciu o wynikową wartość z sieci i prawdziwą (docelową) wartość.
2. **Przejście w tył** (propagacja wsteczna) - wyznaczenie **gradientu funkcji  straty** $\mathcal{L}$ **względem parametrów sieci** $\theta$.
3. Krok optymalizacji parametrów sieci - zmiana w kierunku przeciwnym do gradientu.

##Przygotowanie środowiska
Upewnij się, że notatnik jest uruchomiony na maszynie z GPU. Jeśli GPU nie jest dostępne zmień typ maszyny (Runtime | Change runtime type) i wybierz T4 GPU.

In [1]:
!nvidia-smi

Sun Mar 16 14:07:41 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   60C    P8             10W /   70W |       0MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

Biblioteka PyTorch (`torch`) jest domyślnie zainstalowana w środowisku COLAB.

In [2]:
import torch
import numpy as np

print(f"Wersja biblioteki PyTorch: {torch.__version__}")

Wersja biblioteki PyTorch: 2.6.0+cu124


Sprawdzenie dostępnego urządzenia GPU.

In [7]:
print(f"Dostępność GPU: {torch.cuda.is_available()}")
print(f"Typ GPU: {torch.cuda.get_device_name(0)}")

Dostępność GPU: True
Typ GPU: Tesla T4


Instalacja pakietu torchviz do wizualizacji grafów obliczeń ([link](https://github.com/szagoruyko/pytorchviz)).

In [4]:
!pip install -q torchviz

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 61.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 16.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 28.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 10.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 6.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 63.2 MB/s eta 0:00:00


#Automatyczne różniczkowanie (`torch.autograd`)

**Gradient** (lub gradientowe pole wektorowe) funkcji skalarnej wielu zmiennych $
f: \mathbb{R}^D → \mathbb{R}
$ oznaczamyy
$\nabla f$ (czytaj: nabla).
W układzie współrzędnych kartezjańskich gradient jest wektorem, którego składowe są pochodnymi cząstkowymi funkcji $f$:
$$\nabla f=\left[{\frac {\partial f}{\partial x_{1}}},\dots ,{\frac {\partial f}{\partial x_{n}}}\right]$$

Niech $\mathcal{L}: \mathbb{R}^D \rightarrow \mathbb{R}$ będzie pewną funkcją straty określoną dla sieci neuronowej o $D$ parametrach (wagach).
Celem treningu sieci neuronowej jest znalezienie zestawu parametrów $\mathbf{\hat{}} \in \mathbb{R}^D$ minimalizującego wartośc funkcji straty:
$$\mathbf{\hat{w}} = \arg \min_{\textbf{w}} \mathcal{L} \left( \textbf{w} \right)$$
W metodzie **spadku wzdłuż gradientu** zaczynamy od losowo zainicjalizowanych parametrów (wag) sieci $\textbf{w}_0$ a następnie iteracyjnie aktualizujemy parametry sieci w kierunku przeciwnym do wartości gradientu:
$$
\mathbf{w}_{t+1} = \mathbf{w}_{t} - \eta \nabla \mathcal{L} \left( \mathbf{w}_t \right)
$$.





Aby wyznaczyć **gradient funkcji straty względem parametrów sieci**, PyTorch posiada wbudowany mechanizm różniczkowania o nazwie `torch.autograd`. Umożliwia on automatyczne obliczanie gradientu dla dowolnego grafu obliczeniowego.

Obiekty typu Tensor posiadają logiczną flagę `requires_grad`.
Domyślnie flaga `requires_grad` jest ustawiana na `False`.
Po jej włączeniu PyTorch będzie automatycznie budował grafy dla wszystkich obliczeń wykonanych z wykorzystaniem tego tensora aby umożliwić automatyczne wyznaczanie gradientu.
Jeśli jeden z argumentów operacji na tensorach ma ustawioną flagę `requires_grad`, wynik również będzie miał ustawioną tę flagę.

#Zadania do wykonania

##Zadanie 1

Niech $f: \mathbb{R}^2 \rightarrow \mathbb{R}$ będzie funkcją:

$$f(x) = sin(x_1) cos(x_2) + sin(0.5 \cdot x_1) cos(0.5 \cdot x_2)$$.

1.   Napisz kod wyznaczających lokalne minimum funkcji $f$ metodą spadku wzdłuż gradientu dla początkowych wartości argumentów $x_1, x_2$ wylosowanych z zakresu $[0; 10]$. Wyświetl znalezione minimum oraz wartości argumentów funcji.
    *   Wykorzystaj mechanizm autoróżniczkowania do wyznaczenia gradientu funkcji $f$. Pamiętaj, aby włączyć budowanie grafu obliczeń dla tensorów `x1` i `x2`.
    *   Liczbę iteracji i stopę uczenia dobierz eksperymentalnie.
    *   Na końcu każdego kroku optymalizacji wyzeruj wartości gradientów każdego z argumentów (`x.grad.zeros_()`). Domyślnie PyTorch akumuluje wartości gradientu dla wielu wywołań przejścia w tył `backward()`.
2.   Zwizualizuj trajektorie parametrów $(x_1, x_2)$ w kolejnych krokach optymalizacji powtarzając cały proces kilkakrotnie, rozpoczynając od losowo wybranych wartości argumentów, każdy z zakresu $[0; 10]$. Czy za każdym razem osiągane jest to samo lokalne minimum?
3.   (opcjonalnie) Zaimplementuj zwektoryzowaną wersję procedury wykonującej minimalizację wartości funkcji $f$ dla wielu zestawów argumentów wejściowych danych jako macierz (tensor) o wymiarach $(n,2)$.
   *   Zwektoryzowana wersja nie zawiera pętli przechodzącej po każdym z $n$ zestawów argumentów. W jednym kroku optymalizacji aktualizuje wszystkie $n$ zestawów argumentów.
   *   Aby wyznaczyć gradient dla każdego elementu z osobna tensora który nie jest skalarem, np. dla $n$-elementowego wektora `f` zawierającego wyniki obliczeń dla $n$ zestawów argumentów, jako argument metody `backward` podaj tensor jedynek o rozmiarze równym rozmiarowi `f`, np. `f.backward(torch.ones_like(f))`.

Wizualizacja funkcji $f(x)$ z wykorzystaniem biblioteki Plotly.

In [5]:
import numpy as np
import plotly.graph_objects as go

# Utwórz siatkę wartości x i y
x = np.linspace(0, 10, 100)
y = np.linspace(0, 10, 100)
X, Y = np.meshgrid(x, y)
Z = np.sin(X) * np.cos(Y) + np.sin(0.5 * X) * np.cos(0.5 * Y)

fig = go.Figure(data=go.Contour(z=Z, x=x, y=y, colorscale='Viridis'))
fig.update_layout(title="Izolinie funkcji 3D", xaxis_title="X", yaxis_title="Y")
fig.show()

In [6]:
fig = go.Figure(data=[go.Surface(z=Z, x=x, y=y, colorscale='Viridis')])
fig.update_layout(
    scene=dict(xaxis_title="X", yaxis_title="Y", zaxis_title="Z")
    )
fig.show()

## 1. Lokalne minimum funkcji

In [8]:
# function f(x1, x2)
def f(x1, x2):
  return torch.sin(x1) * torch.cos(x2) + torch.sin(0.5 *x1) * torch.cos(0.5 * x2)

# random number initialization
def generate_x1_x2():
  x1 = torch.rand(1) * torch.tensor(10)
  x2 = torch.rand(1) * torch.tensor(10)

  return x1, x2

def find_minimum(epochs, learning_rate, x1=None, x2=None, visualize=False):

  records = [] # (x1, x2, y)

  # initialize x1 and x2
  if x1 is None and x2 is None:
    x1, x2 = generate_x1_x2()

  if visualize:
    y = f(x1, x2)
    records.append((x1.item(), x2.item(), y.item()))

  x1.requires_grad = True
  x2.requires_grad = True

  for epoch in range(epochs):
    y = f(x1, x2)

    y.backward()

    with torch.no_grad():
      x1 += -1*learning_rate * x1.grad
      x2 += -1*learning_rate * x2.grad

    x1.grad.zero_()
    x2.grad.zero_()

    if visualize:
      record = (x1.item(), x2.item(), f(x1, x2).item())
      records.append(record)

  if visualize:
    return records

  return x1, x2

def test_different_initialization(tries, epochs, learning_rate):
  for _ in range(tries):
    x1, x2 = find_minimum(epochs, learning_rate)
    value = f(x1, x2)

    print(f"Minimum located at point : x1 = {np.round(x1.item(),2)} and x2 = {np.round(x2.item(),2)} ---- Value of function at this point is : {np.round(value.item(),2)}")



In [ ]:
def find_learning_rate(x1, x2, learning_rates, epochs):
  for lr in learning_rates:
    x1, x2 = find_minimum(epochs, lr, x1, x2)
    value = f(x1, x2)

    print(f"LR : {lr} | X1 : {np.round(x1.item(),2)} | X2 : {np.round(x2.item(),2)} | VALUE : {np.round(value.item(),2)}")


In [ ]:
learning_rates = [0.01, 0.02, 0.03, 0.04, 0.05, 0.08, 0.1, 0.15, 0.2]
epochs = 200

for _ in range(10):
  x1, x2 = generate_x1_x2()
  print(f"Testing minimum for points : {np.round(x1.item(),2)} and {np.round(x2.item(),2)}")
  find_learning_rate(x1, x2, learning_rates, epochs)

Testing minimum for points : 0.78 and 3.61
LR : 0.01 | X1 : 1.51 | X2 : 3.49 | VALUE : -1.06
LR : 0.02 | X1 : 1.63 | X2 : 3.51 | VALUE : -1.06
LR : 0.03 | X1 : 1.64 | X2 : 3.51 | VALUE : -1.06
LR : 0.04 | X1 : 1.64 | X2 : 3.51 | VALUE : -1.06
LR : 0.05 | X1 : 1.64 | X2 : 3.51 | VALUE : -1.06
LR : 0.08 | X1 : 1.64 | X2 : 3.51 | VALUE : -1.06
LR : 0.1 | X1 : 1.64 | X2 : 3.51 | VALUE : -1.06
LR : 0.15 | X1 : 1.64 | X2 : 3.51 | VALUE : -1.06
LR : 0.2 | X1 : 1.64 | X2 : 3.51 | VALUE : -1.06
Testing minimum for points : 8.53 and 9.25
LR : 0.01 | X1 : 7.98 | X2 : 9.74 | VALUE : -1.06
LR : 0.02 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
LR : 0.03 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
LR : 0.04 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
LR : 0.05 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
LR : 0.08 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
LR : 0.1 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
LR : 0.15 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
LR : 0.2 | X1 : 7.92 | X2 : 9.79 | VALUE : -1.06
Testing minimum fo

### Wnoski
- Stopa nauki w wysokości 0.02 jest wystarczajace do znalezienie minimum
- 200 epok jest wystarczające ale 500 daje lepsze efekty w postaci większej pewności trafienia do minimum
- Różne punkty startowe znajdują różne minima
- Bazując na wykresie oraz wynikach szukania minimum, można stwierdzić, że minimum globalne wynosi około -1.76

### Testowanie różnych punktów inicjalizacji dla LR=0.02 oraz 500 epok

In [ ]:
EPOCHS = 500
LR = 0.02
TRIES = 10

test_different_initialization(TRIES, EPOCHS, LR)

Minimum located at point : x1 = 7.92 and x2 = 2.77 ---- Value of function at this point is : -1.06
Minimum located at point : x1 = 4.41 and x2 = 6.28 ---- Value of function at this point is : -1.76
Minimum located at point : x1 = 1.64 and x2 = 3.51 ---- Value of function at this point is : -1.06
Minimum located at point : x1 = 7.92 and x2 = 9.79 ---- Value of function at this point is : -1.06
Minimum located at point : x1 = 7.92 and x2 = 2.77 ---- Value of function at this point is : -1.06
Minimum located at point : x1 = 7.92 and x2 = 9.79 ---- Value of function at this point is : -1.06
Minimum located at point : x1 = 7.92 and x2 = 2.77 ---- Value of function at this point is : -1.06
Minimum located at point : x1 = -1.87 and x2 = 0.01 ---- Value of function at this point is : -1.76
Minimum located at point : x1 = 7.92 and x2 = 2.77 ---- Value of function at this point is : -1.06
Minimum located at point : x1 = 4.41 and x2 = 6.28 ---- Value of function at this point is : -1.76


## 2. Wizualizacja kroków

### 2D PLOT

In [24]:
def visualize_optimization_trace_2d(epochs=500, learning_rate=0.02):
    # contour
    x = np.linspace(0, 10, 100)
    y = np.linspace(0, 10, 100)
    X, Y = np.meshgrid(x, y)
    Z = np.sin(X) * np.cos(Y) + np.sin(0.5 * X) * np.cos(0.5 * Y)

    fig = go.Figure()

    fig.add_trace(go.Contour(z=Z, x=x, y=y, colorscale='Viridis', opacity=0.8))
    records = find_minimum(epochs, learning_rate, visualize=True)

    # extract trajectory points
    x_trace = [r[0] for r in records]
    y_trace = [r[1] for r in records]

    # add trajectory points
    fig.add_trace(go.Scatter(
        x=x_trace[:-1], y=y_trace[:-1],
        mode="markers+lines",
        marker=dict(color='red', size=5),
        name="Optimization Path"
    ))

    # add final point wiht different color
    fig.add_trace(go.Scatter(
        x=[x_trace[-1]], y=[y_trace[-1]],
        mode="markers",
        marker=dict(color='blue', size=10, symbol='x'),
        name="Final Point"
    ))

    fig.update_layout(title="Ścieżka optymalizacji metody gradientowej",
                      xaxis_title="X1", yaxis_title="X2",
                      legend=dict(x=1.1))


    fig.show()

# Run visualization for different starting points
for _ in range(6):
  visualize_optimization_trace_2d()

### 3D PLOT

In [ ]:
def visualize_optimization_trace_3d(epochs=500, learning_rate=0.02):
    # contour
    x = np.linspace(0, 10, 100)
    y = np.linspace(0, 10, 100)
    X, Y = np.meshgrid(x, y)
    Z = np.sin(X) * np.cos(Y) + np.sin(0.5 * X) * np.cos(0.5 * Y)

    fig = go.Figure()

    fig.add_trace(go.Surface(z=Z, x=X, y=Y, colorscale='Viridis', opacity=0.8))

    records = find_minimum(epochs, learning_rate, visualize=True)

    # trajectory points
    x_trace = [r[0] for r in records]
    y_trace = [r[1] for r in records]
    z_trace = [r[2] for r in records]

  # add trajectory path
    fig.add_trace(go.Scatter3d(
        x=x_trace[:-1], y=y_trace[:-1], z=z_trace[:-1],
        mode="markers+lines",
        marker=dict(color='red', size=5),
        line=dict(color='red', width=2),
        name="Optimization Path"
    ))

    # add final point with different color
    fig.add_trace(go.Scatter3d(
        x=[x_trace[-1]], y=[y_trace[-1]], z=[z_trace[-1]],
        mode="markers",
        marker=dict(color='blue', size=8, symbol='x'),
        name="Final Point"
    ))

    fig.update_layout(
        title="Ścieżka optymalizacji metody gradientowej w 3D",
        scene=dict(
            xaxis_title="X1",
            yaxis_title="X2",
            zaxis_title="f(X1, X2)"
        ),
        legend=dict(x=1.1)
    )

    fig.show()

for _ in range(6):
  visualize_optimization_trace_3d()


# 3. Wekotryzajca

In [11]:
def find_minimum_vectorized(epochs, learning_rate, n_points=10):
    points = torch.rand(n_points, 2) * torch.tensor(10)
    points.requires_grad = True

    starting_points = points.clone().detach()

    for epoch in range(epochs):
        y = f(points[:, 0], points[:, 1])
        y.backward(torch.ones_like(y))

        with torch.no_grad():
            points -= learning_rate * points.grad
            points.grad.zero_()

    rounded_points = torch.from_numpy(np.round(points.detach().numpy(),2))
    starting_points = torch.from_numpy(np.round(starting_points.detach().numpy(),2))

    values = f(rounded_points[:, 0], rounded_points[:,1])
    values = torch.from_numpy(np.round(values.detach().numpy(),2))


    return rounded_points, starting_points, values

optimized_points, starting_points, values = find_minimum_vectorized(epochs=500, learning_rate=0.02, n_points=10)
print("Starting points:\n", starting_points)
print("Optimized points:\n", optimized_points)
print("Values :\n", values)


Starting points:
 tensor([[0.5300, 2.0500],
        [1.4700, 7.4200],
        [3.1000, 7.3500],
        [5.2100, 5.4000],
        [8.5600, 8.8700],
        [6.4200, 6.3000],
        [1.1300, 6.9000],
        [0.5000, 2.4700],
        [4.8800, 4.9400],
        [7.9600, 9.3300]])
Optimized points:
 tensor([[1.6400, 3.5100],
        [1.6400, 9.0600],
        [4.4100, 6.2800],
        [4.4100, 6.2800],
        [7.9200, 9.7900],
        [4.4100, 6.2800],
        [1.6400, 9.0600],
        [1.6400, 3.5100],
        [4.4100, 6.2800],
        [7.9200, 9.7900]])
Values :
 tensor([-1.0600, -1.0600, -1.7600, -1.7600, -1.0600, -1.7600, -1.0600, -1.0600,
        -1.7600, -1.0600])
